### Álvaro Plata, Brenda Barahona, Sofía Álvarez (201729031)

In [1]:
# ESAI

# Importamos todas las librerias necesarias para el laboratorio.
import numpy as np
import pandas as pd
from pandas_profiling import ProfileReport

<h1 align='center'>Laboratorio 1: Inteligencia de Negocios</h1>

SaludAlpes es una entidad de salud colombiana que se especializa en atender pacientes diagnosticados con diabetes.
Entre las actividades principales de SaludAlpes se destaca el análisis de resultados de laboratorio para la detección de diabetes.
Este servicio de diagnóstico implica el análisis manual por parte de médicos especialistas, a partir de los resultados de exámenes de laboratorio, lo cual ha generado en los últimos años, una serie de problemas asociados con los tiempos de atención a estos pacientes, causada por demoras en la confirmación del diagnóstico.
SaludAlpes los ha contratado para agilizar y mejorar el proceso de análisis de resultados clínicos de tal manera que se reduzcan los tiempos de confirmación de diagnóstico y se agilice el inicio del tratamiento a paciente con diabetes confirmada.
Su labor como consultor de BI es agilizar el proceso de confirmación de diagnóstico de diabetes en un paciente, utilizando datos históricos y realizando sobre ellos procesos de análisis y procesamiento, al igual que comunicando los resultados a la entidad para afianzar sus conocimientos en áreas de aprendizaje automático y al mismo tiempo generar una ventaja competitiva.
Con el fin de lograr el objetivo para el cual fue contratado, SaludAlpes espera tener tres modelos distintos de clasificación, construidos con 3 técnicas diferentes, entre las cuales deben estar árboles de decisión y KNN (k-nearest-neighbours). De igual manera, espera que siga la metodología que ellos utilizan en la actualidad para el desarrollo de ese tipo de proyectos,
para lo cual le sugiere realizar los siguientes pasos:

### 1. Análisis exploratorio y perfilamiento de los datos.

Para poder realizar un buen algoritmo de Machine Learning, lo primero que debemos hacer es analizar y perfilar los datos, con el fin de prepararlos para 

Lo primero que hacemos es leer los datos:

In [2]:
datos = pd.read_csv('202210_Laboratorio1_data_Datos_Clasificacion_2022.csv', delimiter=';', low_memory=False)

Cabe anotar que en este caso, debemos poner el atributo de baja memoria en False. Un warning decía que hay tipos de datos mixtos y, para evitarlo, debíamos hacer eso con el parámetro de la función <code>pd.read_csv()</code>.

Una vez leídos los datos, podemos ver la cantidad de columnas (features) y datos (filas) que tiene nuestro conjunto de datos:

In [3]:
datos.shape

(100000, 27)

En principio, nuestro conjunto de datos cuenta con 100.000 registros y 27 columnas. Veamos una muestra aleatoria de 5 datos del dataset:

In [4]:
display(datos.sample(5))

Diabetes_012 HighBP HighChol CholCheck BMI Smoker Stroke  \
97609            0      1        1         1  23      1      0   
89206            0      1        0         1  31      0      0   
63425            0      0        0         1  34      1      0   
79075            0      0        0         1  38      0      0   
66321            0      0        0         1  24      0      0   

      HeartDiseaseorAttack PhysActivity Fruits  ... DiffWalk Sex Age  \
97609                    1            1      1  ...        1   0   9   
89206                    0            1      1  ...        0   0   8   
63425                    0            0      1  ...        0   1   4   
79075                    0            1      0  ...        0   0   3   
66321                    0            0      1  ...        0   0   3   

      Education Income Unnamed: 22 Unnamed: 23 Unnamed: 24 Unnamed: 25  \
97609         4      4         NaN         NaN         NaN         NaN   
89206         6      8         NaN         NaN         NaN         NaN   
63425         6      8         NaN         NaN         NaN         NaN   
79075         4      5         NaN         NaN         NaN         NaN   
66321         6      8         NaN         NaN         NaN         NaN   

      Unnamed: 26  
97609         NaN  
89206         NaN  
63425         NaN  
79075         NaN  
66321         NaN  

[5 rows x 27 columns]

En principio, podemos intuir que la variable objetivo será <code>Diabetes_012</code>, porque de acuerdo con el diccionario del negocio, es la que nos permitirá saber si un paciente tiene diabetes, prediabetes, o ninguna condición.

**Nota:** Es importante anotar que lo primero que intentamos hacer fue un _pandas profiling_. No obstante, debido a que hay diversos tipos de datos en las columnas, este arroja varios errores. Por ello, debemos realizar un análisis exploratorio y corregir estas cuestiones antes de utilizar la herramienta.

Podemos ver que al final de esta muestra hay 5 columnas que aparecen sin nombre: Unnamed:22 hasta Unnamed:26, cuyos valores están todos en NaN. Por ello, decidimos revisar las otras columnas del dataframe y compararlas con el diccionario de datos dado para este laboratorio.

In [5]:
print(list(datos.columns))

['Diabetes_012', 'HighBP', 'HighChol', 'CholCheck', 'BMI', 'Smoker', 'Stroke', 'HeartDiseaseorAttack', 'PhysActivity', 'Fruits', 'Veggies', 'HvyAlcoholConsump', 'AnyHealthcare', 'NoDocbcCost', 'GenHlth', 'MentHlth', 'PhysHlth', 'DiffWalk', 'Sex', 'Age', 'Education', 'Income', 'Unnamed: 22', 'Unnamed: 23', 'Unnamed: 24', 'Unnamed: 25', 'Unnamed: 26']


Contrastando los nombres de las columnas con el diccionario, vemos que las columnas 'Unnamed: 22', 'Unnamed: 23', 'Unnamed: 24', 'Unnamed: 25' y 'Unnamed: 26' no están caracterizadas por el negocio y, por tanto, no nos dan información relevante para el modelo. Más aún, podemos ver los valores únicos de cada una de estas columnas.

In [6]:
# Iteramos de 22 a 26 para conocer los valores únicos de cada una de las columnas Unnamed.
for i in range(22,27):
    print(datos['Unnamed: {num}'.format(num=i)].unique(), end=' ')

[nan] [nan] [nan] [nan] [nan] 

Vemos entonces que estas columnas están llenas de <code>NaN</code>; i.e. Not a Number. Por tanto, no aportan nada y procedemos a eliminarlas de nuestro conjunto de datos:

In [7]:
# Eliminamos las últimas columnas
datos = datos.drop(['Unnamed: {num}'.format(num=i) for i in range(22,27)], axis=1)

Revisamos que las columnas hayan sido correctamente eliminadas:

In [8]:
print(list(datos.columns))

['Diabetes_012', 'HighBP', 'HighChol', 'CholCheck', 'BMI', 'Smoker', 'Stroke', 'HeartDiseaseorAttack', 'PhysActivity', 'Fruits', 'Veggies', 'HvyAlcoholConsump', 'AnyHealthcare', 'NoDocbcCost', 'GenHlth', 'MentHlth', 'PhysHlth', 'DiffWalk', 'Sex', 'Age', 'Education', 'Income']


Ahora, ya tenemos todas las columnas que se encuentran en el diccionario. Lo siguiente que queremos ver es explorar los datos que hay en nuestro dataset. Nos preguntamos: ¿Por qué, al comienzo, tuvimos un _warning_ con los tipos de datos? ¿Qué datos están almacenados en el conjunto?

Revisando el diccionario de datos, nos dimos cuenta de que todos los atributos debían ser numéricos (así fueran categorías numéricas - como es el caso de columnas como GenHlth, Age y Education, entre otras - o binarias). Se nos ocurrió, entonces, revisar si las columnas estaban presentando otro tipo de datos no numéricos. Para ello, primero buscamos en el conjunto de datos todos los valores distintos que hay en nuestro dataframe y los convertimos en una lista. Luego, iteramos sobre ellos e intentamos convertirlos (hacer el cast) a números flotantes, usando un bloque try-except. Si se lanza una excepción, significa que el dato no es numérico y lo agregamos a la lista, para saber qué otro tipo de datos tiene nuestro dataframe.

In [9]:
# Vemos todos los valores distintos (únicos) que tiene el dataframe.
valores_distintos = list(datos.apply(pd.value_counts).index)
valores_no_numericos = []
# Interamos sobre los valores distintos
for val in valores_distintos:
    try:
        # Intentamos hacer el cast a float
        numero = float(val)
    except:
        # Si hay datos no numericos, los agregamos a la lista
        valores_no_numericos.append(val)
print('Los valores no numéricos son: {}'.format(valores_no_numericos))

Los valores no numéricos son: ['-', '?', 'Xx']


Del procedimiento anterior, podemos ver que hay 3 tipos de datos no numéricos en todo el dataframe.

Debemos tomar una decisión sobre si completamos estos datos con medidas de tendencia central (en este caso, como la moda, porque son atributos categóricos), o si los eliminamos. Para tomar estas decisiones, debemos saber en cuántos datos del conjunto total hay estas inconsistencias. 

Es importante anotar que vamos fila por fila en el conjunto de datos porque, si revisamos en columnas (por ejemplo, usando las funcionalidades de <code>pandas</code>: <code>datos[columna] == '-'</code>) puede ocurrir que, para el mismo dato en otra columna, haya otro '-', o una 'Xx' y un '?'. Esto es difícil saberlo en pandas y, por ello, recorremos todo el conjunto de datos.

In [10]:
num_inconsistentes = len(datos[((datos.values == '-')|(datos.values == '?')|(datos.values == 'Xx')).any(axis=1)])
print('El número de datos inconsistentes es: {}'.format(num_inconsistentes))

El número de datos inconsistentes es: 740


**NOTA:**  El código de la celda de arriba hace lo mismo que el snippet de código mostrado a continuación:

```python
num_inconsistentes = 0
for line in datos.values:
    if ('-' in line) or ('?' in line) or ('Xx' in line):
        # Suma uno si hay alguno de estos símbolos. 
        num_inconsistentes += 1
```

Calculamos el porcentaje de datos inválidos con respecto al tamaño del conjunto de datos. Note que en este punto consideramos inválidos todos aquellos datos que no son categóricos, aún no hemos evaluado las restricciones individuales de cada columna.

In [11]:
porcentaje_invalidos_general = num_inconsistentes*100/len(datos)
print('El porcentaje de datos inválidos es del: {}%'.format(porcentaje_invalidos_general))

El porcentaje de datos inválidos es del: 0.74%


Vemos que el porcentaje de datos con los caracteres <code>-</code>, <code>?</code> y <code>Xx</code> es bastante reducido y, por tanto, debemos eliminarlos del dataset. 

In [12]:
datos.drop(datos[(datos.values == '-') | (datos.values == 'Xx') | (datos.values == '?')].index, inplace=True)

In [13]:
print('El tamaño del nuevo conjunto de datos es: {}'.format(len(datos)))

El tamaño del nuevo conjunto de datos es: 99260


De acuerdo con el diccionario del negocio, ahora las variables deben tener únicamente valores numéricos (enteros, para las categóricas o flotantes, para la variable BMI). Revisemos los tipos de datos del dataset: 

In [17]:
print(datos.dtypes)

Diabetes_012            object
HighBP                  object
HighChol                object
CholCheck               object
BMI                     object
Smoker                  object
Stroke                  object
HeartDiseaseorAttack    object
PhysActivity            object
Fruits                  object
Veggies                 object
HvyAlcoholConsump       object
AnyHealthcare           object
NoDocbcCost             object
GenHlth                 object
MentHlth                object
PhysHlth                object
DiffWalk                object
Sex                     object
Age                     object
Education               object
Income                  object
dtype: object


Podemos ver que todas las columnas son de tipo object; y esto se debe, seguramente, a que hay algunos números que está tomando como tal y, otros, como strings. Revisemos, por ejemplo, la columna <code>Diabetes_012</code>:

In [18]:
print(datos['Diabetes_012'].unique())

['0' '2' '1' nan]


Confirmamos entonces que el conjunto de datos está tomando algunos valores numéricos como strings. Convertimos, entonces, estas columnas a datos numéricos. Todas las convertimos a enteros, excepción hecha de la columna BMI que, por el negocio, puede ser cualquier valor real. Además, nos percatamos de que hay algunos datos que son NaN (i.e. Not a Number). De ellos nos encargaremos más adelante.

De esta forma, convertimos todas las columnas primero a <code>float</code>, porque antes de lidiar con los valores nulos, no podemos pasar la columna a <code>int</code>. Pasaremos todas las columnas a int, excepción hecha de BMI, luego de lidiar con los valores nulos.

In [29]:
# Primero convertimos todas las columnas a float
datos = datos.astype(dtype='float64')

Empecemos a lidiar con los valores nulos. Veamos primero, en total, cuantos valores nulos hay en el dataset:

In [34]:
print(datos.isnull().any(axis = 1).sum())

327


# --> Qué hacemos con los nulos ? LOS BORRAMOS? Es que si nos quedamos con ellos, y son por ejemplo de las clases 1 o 2, estamos perjudicando a la clase minoritaria con la media de todo el conjunto de datos o algo así. O quizá podríamos poner las medidas de tendencia central de solamente esa clase, puede ser otra opción. 

Más adelante, hacemos un <code>Pandas Profiling</code>. Ahora, debido a que corregimos el asunto de los tipos de datos y las inconsistencias, sí podemos generarlos

In [39]:
profiling = ProfileReport(datos)
profiling

Summarize dataset:   0%|          | 0/36 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
# VALORES FUERA DE RANGO
# Pipelines